In [1]:
# Install packages
import pandas as pd
import numpy as np

In [3]:
subapps = pd.read_csv('/Users/sambickel-barlow/Desktop/PP434/Portfolio/CC7/HmaSubapplications.csv')
crosswalk = pd.read_csv('/Users/sambickel-barlow/Desktop/PP434/Portfolio/CC7/COUNTY_ZIP_122017.csv')

In [8]:
# Crosswalk from zip code to county code
subapps_df = subapps.merge(crosswalk , left_on='subapplicantZipCode' , right_on='zip')

In [73]:
# Define a function to ensure that when the "primary" or "secondary" Hazard is unknow if fills in the Hazard type
def hazard(df):
    for i in range(len(df)):
        if ((str(df['primaryHazard'].iloc[i]) == 'nan') | (df['primaryHazard'].iloc[i] == 'Uncategorized')) & ((str(df['secondaryHazard'].iloc[i]) == 'nan') | (df['secondaryHazard'].iloc[i] == 'Uncategorized')):
            df['Hazard'].iloc[i] = df['tertiaryHazard'].iloc[i]
        elif ((str(df['primaryHazard'].iloc[i]) == 'nan') | (df['primaryHazard'].iloc[i] == 'Uncategorized')) & ((str(df['secondaryHazard'].iloc[i]) != 'nan') & (df['secondaryHazard'].iloc[i] != 'Uncategorized')):
            df['Hazard'].iloc[i] = df['secondaryHazard'].iloc[i]
        else:
            df['Hazard'].iloc[i] = df['primaryHazard'].iloc[i]

In [75]:
# Apply the hazarad function to create Hazard column
subapps_df['Hazard'] = ''
hazard(subapps_df)

/var/folders/qz/pj0lh7817m3c9ydwgfrtbtf00000gn/T/ipykernel_89566/4113622737.py:8: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df['Hazard'].iloc[i] = df['primaryHazard'].iloc[i]
/var/folders/qz/pj0lh7817m3c9ydwgfrtbtf00000gn/T/ipykernel_895

In [116]:
# Aggregate claims to the county-Hazard level sum subapplication claims. Remove extraneous columns
FEMA_county_haz = subapps_df[['Hazard' , 'totalSubapplicationAmount' , 'county']].groupby(by = ['county' , 'Hazard']).sum('totalSubapplicationAmount').reset_index()

In [117]:
# Ensure 5 digit county code has leading zeros
FEMA_county_haz['county'] = FEMA_county_haz['county'].apply(lambda x: str(x).zfill(5))

In [126]:
# View hazards and the number of occurances of each hazard
FEMA_county_haz['Hazard'].value_counts()

Hazard
Flooding                                1017
Severe storm                             358
Infrastructure failure                   300
Tornado                                  167
Fire                                     100
Winter storm                              73
Earthquake                                67
Tropical cyclone (Hurricane/Typhoon)      65
Drought                                   56
Dam/Levee break                           56
Landslide/Debris flow                     50
Extreme temperature                       29
Tsunami                                    7
Disease                                    5
Hostile action                             3
Cyber incident                             3
Uncategorized                              2
Biological incident                        2
Chemical incident                          1
Radiological incident                      1
Name: count, dtype: int64

In [136]:
# Crate a dictionary to map Hazard to colors
hazard_colors = {
    'Flooding': '00AAFF',
    'Severe storm': 'FFFF00',
    'Infrastructure failure': '884DFF',
    'Tornado': '4F666A',
    'Fire': 'FF1919',
    'Winter storm': 'A0E6FF',
    'Tropical cyclone (Hurricane/Typhoon)': '00AAFF',
    'Drought': 'CC5500',
    'Dam/Levee break': '00AAFF',
    'Landslide/Debris flow': '644117',
    'Extreme temperature': 'CC5500',
    'Tsunami': '00AAFF'
}


In [137]:
# Create new column mapping hazards to colors
FEMA_county_haz['Hazard_color'] = FEMA_county_haz['Hazard'].apply(lambda x: hazard_colors.get(x, 'FFFFFF'))

In [142]:
# Output to csv
FEMA_county_haz.to_csv('/Users/sambickel-barlow/Desktop/PP434/Portfolio/CC7/FEMA_county_haz.csv' , index=False)